# Exploring the CommaAI Device data

This requires python 3.11 or later because of the usage of the tools folder from Openpilot, which uses 3.11 features

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from PIL import Image
import cv2
import pandas as pd
from pathlib import Path
# This is taken from the Openpilot project
from openpilot.tools.lib.logreader import LogReader, ReadMode
from dataclasses import dataclass
from typing import List
import capnp
import json

/tmp/ipykernel_1798685/291723216.py:5: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [3]:
device_path = Path("/home/ulrikro/datasets/CommaAI/2024-01-14--13-01-26--10/")

# About the folder

Each folder, marked by their data and a number, contains 5 files: ecamera.hevc, fcamera.hevc, qcamera.ts, qlog, rlog. Each file contains 1 min video. 

* ecamera.hevc - road facing wide angle camera 1928*1208 at 20Hz
* fcamera.hevc - road facing narrow camera 1928*1208 at 20Hz
* qcamera.ts - driver facing wide angle camera 526*330 at 20Hz
* qlog - some
* rlog - some



In [4]:
ecamera_path = device_path / "ecamera.hevc"
fcamera_path = device_path / "fcamera.hevc"
qcamera_path = device_path / "qcamera.ts"
qlog_path = device_path / "qlog"
rlog_path = device_path / "rlog"


# Overview of the video files

In [5]:
def read_video_frames(file_path: str):
    frames = []
    video = cv2.VideoCapture(file_path)
    while video.isOpened():
        ret, frame = video.read()
        if not ret:
            break
        frames.append(frame)
    video.release()
    return frames

In [6]:
# ecamera_frames = read_video_frames(ecamera_path.as_posix())
# len(ecamera_frames)

In [7]:
# ecamera_frames[0].shape

In [8]:
# fcamera_frames = read_video_frames(fcamera_path.as_posix())
#len(fcamera_frames)

In [9]:
# fcamera_frames[0].shape

In [10]:
# qcamera_frames = read_video_frames(qcamera_path.as_posix())
# len(qcamera_frames)

In [11]:
# qcamera_frames[0].shape

# Overview of the log files

In [12]:


qlog_data = LogReader(qlog_path.as_posix(), default_mode=ReadMode.QLOG)

In [13]:
qlog_list = list(qlog_data)
len(qlog_list)

11515

In [14]:
type(qlog_list[0])

capnp.lib.capnp._DynamicStructReader

Each iteration throug the log data retruns a capnp.lib.capnp._DynamicStructReader object. 

capnp is a proto schema parsing library 

The proto schema seems to be defined in openpilot/common/params.cc
 


In [15]:
@dataclass
class CommandEntry:
    key: str
    value: str

@dataclass
class Commands:
    entries: List[CommandEntry]

@dataclass
class ParamEntry:
    key: str
    value: str

@dataclass
class Params:
    entries: List[ParamEntry]

@dataclass
class InitData:
    kernelArgs: List[str]
    dongleId: str
    deviceType: str
    version: str
    dirty: bool
    gitCommit: str
    gitBranch: str
    passive: bool
    gitRemote: str
    kernelVersion: str
    params: Params
    osVersion: str
    commands: Commands

@dataclass
class LogData:
    logMonoTime: int
    initData: InitData
    valid: bool
    # these just include a subset of the data

In [16]:
qlog_list: List[LogData] = list(qlog_data)

In [17]:
print([attr for attr in dir(qlog_list[0]) if not attr.startswith("__")])

['_get', '_get_by_field', '_has', '_has_by_field', '_parent', '_which', '_which_str', 'accelerometer', 'accelerometer2', 'androidGnssDEPRECATED', 'androidLog', 'applanixLocationDEPRECATED', 'applanixRawDEPRECATED', 'as_builder', 'boot', 'cameraOdometry', 'can', 'carControl', 'carParams', 'carState', 'cellInfoDEPRECATED', 'clocks', 'controlsState', 'customReserved0', 'customReserved1', 'customReserved2', 'customReserved3', 'customReserved4', 'customReserved5', 'customReserved6', 'customReserved7', 'customReserved8', 'customReserved9', 'customReservedRawData0', 'customReservedRawData1', 'customReservedRawData2', 'deviceState', 'driverCameraState', 'driverEncodeData', 'driverEncodeIdx', 'driverMonitoringState', 'driverStateDEPRECATED', 'driverStateV2', 'errorLogMessage', 'ethernetDataDEPRECATED', 'featuresDEPRECATED', 'gnssMeasurements', 'gpsLocation', 'gpsLocationExternal', 'gpsNMEA', 'gpsPlannerPlanDEPRECATED', 'gpsPlannerPointsDEPRECATED', 'gyroscope', 'gyroscope2', 'initData', 'is_roo

In [18]:
print(str(qlog_list[0].initData.params.entries[0].value))

b'{"alias": null, "athena_host": "prod-comma-public-athena-0.prod-comma-public-athena.production.svc.cluster.local", "device_type": "threex", "dongle_id": "45ba82b7ecf23784", "ignore_uploads": null, "last_athena_ping": 1705231623, "last_gps_accuracy": null, "last_gps_bearing": null, "last_gps_lat": null, "last_gps_lng": null, "last_gps_speed": null, "last_gps_time": null, "public_key": "-----BEGIN PUBLIC KEY-----\\nMIIBIjANBgkqhkiG9w0BAQEFAAOCAQ8AMIIBCgKCAQEA5tgJB/RQmWgUQlIQBG6H\\ncPB65/ZjQJMxeQpZeaPvBrHGmIKybjnirGDgEqlfa1bTzSfXC8LbNu73J9qXbDM6\\nKnJ3Zh6M4NAFtAd/g04vWbEhmg/3ff2Abjq2sKolEDIyGBwli16usZEvGBAsuQpt\\nElxgVyx1TrLxHux9sZ++5sQce12gkhkiaItT26X7QOvjEwqTjP/LN3E4yUQNbAoq\\nhiDpcWgVQDT04HbMqIITvpOjd5sXLXhqr01sqoNVli69SwgjGyaN3eSAx4C2OiFw\\nwsc6gED93kOcVJmYeTahpfmJ0zRTgccDPC6eNHoTTVmnrZIhCqnm532a4bDbjN9z\\nnQIDAQAB\\n-----END PUBLIC KEY-----\\n", "serial": "9e856db5", "sim_id": "", "trial_claimed": true, "is_paired": true, "eligible_features": {"prime": true, "prime_data": true, "na

In [19]:
qlog_list[0].to_dict()

{'initData': {'kernelArgs': ['rcupdate.rcu_expedited=1',
   'console=ttyMSM0,115200n8',
   'quiet',
   'loglevel=3',
   'earlycon=msm_geni_serial,0xA84000',
   'androidboot.hardware=qcom',
   'androidboot.console=ttyMSM0',
   'video=DSI-1:1080x2160@60e',
   'ehci-hcd.park=3',
   'lpm_levels.sleep_disabled=1',
   'service_locator.enable=1',
   'androidboot.selinux=permissive',
   'firmware_class.path=/lib/firmware/updates',
   'net.ifnames=0',
   'dyndbg=""',
   'root=/dev/sda6',
   'androidboot.bootdevice=1d84000.ufshc',
   'androidboot.serialno=9e856db5',
   'androidboot.baseband=sda',
   'msm_drm.dsi_display0=dsi_fhd_ea8074_1080_cmd_display:',
   'androidboot.slot_suffix=_a',
   'skip_initramfs',
   'rootwait',
   'ro',
   'init=/sbin/init'],
  'dongleId': '45ba82b7ecf23784',
  'deviceType': 'tizi',
  'version': '0.9.5-release',
  'dirty': False,
  'gitCommit': '0df64642759d61f59cc6f09b598ddadb7df96459',
  'gitBranch': 'release3',
  'passive': False,
  'gitRemote': 'https://github.co

In [20]:
def isiterable(item):
    try:
        iter(item)
        return True
    except TypeError:
        return False
def get_fields(o, print_progress=True, depth=0):
    if isinstance(o, list) or isinstance(o, tuple) or isinstance(o, set) or isiterable(o):
        fields = []
        for item in o:
            field = get_fields(item, print_progress, depth=depth+1)
            fields.append(field)
        return fields
    elif isinstance(o, dict):
        total_dict = dict()
        for key, value in o.items():
            total_dict[key] = get_fields(value, print_progress, depth=depth+1)
        return total_dict
    elif isinstance(o, str) or isinstance(o, int) or isinstance(o, float) or isinstance(o, bool) or isinstance(o, bytes) or o is None:
        return type(o).__name__
    else:
        item_attrs = [attr for attr in dir(o) if not attr.startswith("_")]
        # print("item_attrs", item_attrs)
        total_dict = dict()
        progress = 0
        for attr in item_attrs:
            if print_progress:
                progress += 1
                print(f"Progress {depth}: {progress}/{len(item_attrs)} attr={attr}", end="\r")
            try: 
                total_dict[attr] = get_fields(getattr(o, attr), print_progress, depth=depth+1)
            except Exception:
                continue
        return total_dict
        
        

In [21]:
import re

def parse_capnp_string(s: str):
    # Wrap words after = that are not numbers or true of false in quotes
    s = re.sub(r'(?<=\s=\s)(?!true|false|\d+)(\w+)', r'"\1"', s)
    # Wrap in quotes and replace = with :
    s = re.sub(r"(\w+) = ", r'"\1": ', s)

    # Replace ( with [ for lists
    pattern = r'\((?:"[^"]*"|\d+)(?:\s*,\s*(?:"[^"]*"|\d+))*\)'

    def convert(match):
        inner_text = match.group(0)[1:-1]  # Remove the outer parentheses
        return "[" + inner_text + "]"  # Surround with square brackets

    s = re.sub(pattern, convert, s)

    # Replace the rest of the parentheses with curly braces and remove newlines
    s = s.replace("(", "{").replace(")", "}").replace("\n", "")
    return s

In [22]:
# import json
# field_json = capnp_to_json(str(qlog_list[0]))
# field_json
# parse_custom_structure(str(qlog_list[0]))

In [23]:
qlog_list[0].to_dict()

{'initData': {'kernelArgs': ['rcupdate.rcu_expedited=1',
   'console=ttyMSM0,115200n8',
   'quiet',
   'loglevel=3',
   'earlycon=msm_geni_serial,0xA84000',
   'androidboot.hardware=qcom',
   'androidboot.console=ttyMSM0',
   'video=DSI-1:1080x2160@60e',
   'ehci-hcd.park=3',
   'lpm_levels.sleep_disabled=1',
   'service_locator.enable=1',
   'androidboot.selinux=permissive',
   'firmware_class.path=/lib/firmware/updates',
   'net.ifnames=0',
   'dyndbg=""',
   'root=/dev/sda6',
   'androidboot.bootdevice=1d84000.ufshc',
   'androidboot.serialno=9e856db5',
   'androidboot.baseband=sda',
   'msm_drm.dsi_display0=dsi_fhd_ea8074_1080_cmd_display:',
   'androidboot.slot_suffix=_a',
   'skip_initramfs',
   'rootwait',
   'ro',
   'init=/sbin/init'],
  'dongleId': '45ba82b7ecf23784',
  'deviceType': 'tizi',
  'version': '0.9.5-release',
  'dirty': False,
  'gitCommit': '0df64642759d61f59cc6f09b598ddadb7df96459',
  'gitBranch': 'release3',
  'passive': False,
  'gitRemote': 'https://github.co

In [24]:
import base64
class BytesEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, bytes):
            # Encode bytes to a Base64 string
            return base64.b64encode(obj).decode('ascii')
        # Let the base class default method raise the TypeError
        return json.JSONEncoder.default(self, obj)

def capnp_to_json_valid_dict(obj):
    json_string = json.dumps(obj.to_dict(), cls=BytesEncoder)
    return json.loads(json_string)
            

In [25]:
qlog_dicts = [capnp_to_json_valid_dict(o) for o in qlog_list]

In [26]:
# jsons = [json.dumps(qlog_dict, indent=4) for qlog_dict in qlog_dicts]
with open("qlog.json", "w") as f:
    json.dump(qlog_dicts, f, indent=4)

In [27]:
for field in list(qlog_list[0].schema.node.struct.fields):
    print(field.name)

logMonoTime
initData
roadCameraState
gpsNMEA
sensorEventDEPRECATED
can
deviceState
controlsState
liveEventDEPRECATED
model
featuresDEPRECATED
sensorEventsDEPRECATED
pandaStateDEPRECATED
radarState
liveUIDEPRECATED
roadEncodeIdx
liveTracks
sendcan
logMessage
liveCalibration
androidLog
gpsLocation
carState
carControl
longitudinalPlan
liveLocationDEPRECATED
ethernetDataDEPRECATED
navUpdateDEPRECATED
cellInfoDEPRECATED
wifiScanDEPRECATED
androidGnssDEPRECATED
qcomGnss
lidarPtsDEPRECATED
procLog
ubloxGnss
clocks
liveMpcDEPRECATED
liveLongitudinalMpcDEPRECATED
navStatusDEPRECATED
ubloxRaw
gpsPlannerPointsDEPRECATED
gpsPlannerPlanDEPRECATED
applanixRawDEPRECATED
trafficEventsDEPRECATED
liveLocationTimingDEPRECATED
orbslamCorrectionDEPRECATED
liveLocationCorrectedDEPRECATED
orbObservationDEPRECATED
gpsLocationExternal
locationDEPRECATED
uiNavigationEventDEPRECATED
liveLocationKalmanDEPRECATED
testJoystick
orbOdometryDEPRECATED
orbFeaturesDEPRECATED
applanixLocationDEPRECATED
orbKeyFrameDEPRECA

In [28]:
result = parse_capnp_string(str(qlog_list[0]))
result

'{ "logMonoTime": 549368898434,  "initData": {    "kernelArgs": [      "rcupdate.rcu_expedited=1",      "console=ttyMSM0,115200n8",      "quiet",      "loglevel=3",      "earlycon=msm_geni_serial,0xA84000",      "androidboot.hardware=qcom",      "androidboot.console=ttyMSM0",      "video=DSI-1:1080x2160@60e",      "ehci-hcd.park=3",      "lpm_levels.sleep_disabled=1",      "service_locator.enable=1",      "androidboot.selinux=permissive",      "firmware_class.path=/lib/firmware/updates",      "net.ifnames=0",      "dyndbg=\\"\\"",      "root=/dev/sda6",      "androidboot.bootdevice=1d84000.ufshc",      "androidboot.serialno=9e856db5",      "androidboot.baseband=sda",      "msm_drm.dsi_display0=dsi_fhd_ea8074_1080_cmd_display:",      "androidboot.slot_suffix=_a",      "skip_initramfs",      "rootwait",      "ro",      "init=/sbin/init" ],    "dongleId": "45ba82b7ecf23784",    "deviceType": "tizi",    "version": "0.9.5-release",    "dirty": false,    "gitCommit": "0df64642759d61f59cc6f09

In [29]:
import json
#json.loads(result)

In [30]:
model_qlogs = [log for log in qlog_list if log.which() == "modelV2"]
len(model_qlogs)

30

In [31]:
print(model_qlogs[3])

( logMonoTime = 1157092048359,
  valid = true,
  modelV2 = (
    frameId = 12124,
    frameAge = 0,
    frameDropPerc = 0,
    timestampEof = 1157054624400,
    position = (
      x = [-1.5592933, -1.4079607, -0.94034994, -0.15331817, 0.94597781, 2.3502755, 4.0572281, 6.0816054, 8.4199743, 11.076779, 14.033125, 17.309542, 20.904549, 24.821371, 29.01038, 33.533928, 38.38641, 43.53376, 49.012196, 54.781616, 60.868141, 67.290619, 74.051605, 81.10144, 88.533752, 96.25666, 104.33369, 112.71635, 121.48546, 130.49567, 140.00322, 149.6834, 159.83925],
      y = [0.14344487, 0.14307681, 0.14316955, 0.14308006, 0.14098066, 0.13810413, 0.13371153, 0.12756485, 0.12173094, 0.11274366, 0.10223039, 0.090855211, 0.077490106, 0.060879104, 0.045715623, 0.030229293, 0.017647684, 0.014660567, 0.016167995, 0.033507023, 0.074235037, 0.13414395, 0.22833961, 0.34605789, 0.51319385, 0.70221877, 0.94211924, 1.2192439, 1.5349848, 1.9019217, 2.3123288, 2.7670474, 3.3022468],
      z = [-0.0004885589, -0.000652969

# The different types of CAN messages

In [32]:
types = [item.which() for item in qlog_list]
len(types)

11515

In [33]:
qlog_types = set(types)
len(qlog_types)

43

In [34]:
qlog_types

{'accelerometer',
 'cameraOdometry',
 'can',
 'carControl',
 'carParams',
 'carState',
 'controlsState',
 'deviceState',
 'driverCameraState',
 'driverEncodeIdx',
 'driverMonitoringState',
 'driverStateV2',
 'gpsLocation',
 'gyroscope',
 'initData',
 'lateralPlanDEPRECATED',
 'liveCalibration',
 'liveLocationKalman',
 'liveParameters',
 'liveTorqueParameters',
 'longitudinalPlan',
 'magnetometer',
 'managerState',
 'mapRenderState',
 'microphone',
 'modelV2',
 'navInstruction',
 'navModel',
 'onroadEvents',
 'pandaStates',
 'peripheralState',
 'procLog',
 'qRoadEncodeIdx',
 'radarState',
 'roadCameraState',
 'roadEncodeIdx',
 'sentinel',
 'temperatureSensor',
 'thumbnail',
 'uiDebug',
 'uiPlan',
 'wideRoadCameraState',
 'wideRoadEncodeIdx'}

Which of these are the most interesting to look at? 


1. modelV2


# RLOG



In [35]:
rlog_data = LogReader(rlog_path.as_posix(), default_mode=ReadMode.RLOG)
rlog_list = list(rlog_data)
rlog_types = set([item.which() for item in rlog_list])

In [36]:
len(qlog_types), len(rlog_types)

(43, 48)

In [37]:
qlog_types == rlog_types

False

In [38]:
len(rlog_list)

64702

In [39]:
# Create rlog json file
# rlog_dicts = [capnp_to_json_valid_dict(o) for o in rlog_list]
# with open("rlog.json", "w") as f:
#     json.dump(rlog_dicts, f, indent=4)

In [40]:
len(rlog_types)

48

In [41]:
rlog_types - qlog_types

{'androidLog', 'liveTracks', 'logMessage', 'navThumbnail', 'qcomGnss'}

In [42]:
rlog_types

{'accelerometer',
 'androidLog',
 'cameraOdometry',
 'can',
 'carControl',
 'carParams',
 'carState',
 'controlsState',
 'deviceState',
 'driverCameraState',
 'driverEncodeIdx',
 'driverMonitoringState',
 'driverStateV2',
 'gpsLocation',
 'gyroscope',
 'initData',
 'lateralPlanDEPRECATED',
 'liveCalibration',
 'liveLocationKalman',
 'liveParameters',
 'liveTorqueParameters',
 'liveTracks',
 'logMessage',
 'longitudinalPlan',
 'magnetometer',
 'managerState',
 'mapRenderState',
 'microphone',
 'modelV2',
 'navInstruction',
 'navModel',
 'navThumbnail',
 'onroadEvents',
 'pandaStates',
 'peripheralState',
 'procLog',
 'qRoadEncodeIdx',
 'qcomGnss',
 'radarState',
 'roadCameraState',
 'roadEncodeIdx',
 'sentinel',
 'temperatureSensor',
 'thumbnail',
 'uiDebug',
 'uiPlan',
 'wideRoadCameraState',
 'wideRoadEncodeIdx'}

## Exploring the rlog data fields

In [43]:
# accelerometer
accelerometer = [log for log in rlog_list if log.which() == "accelerometer"]
accelerometer[0].accelerometer.to_dict()

{'acceleration': {'v': [10.124346733093262,
   0.666414201259613,
   0.7370672821998596],
  'status': 1},
 'version': 1,
 'sensor': 1,
 'type': 1,
 'timestamp': 1150993498933,
 'source': 'lsm6ds3trc',
 'uncalibratedDEPRECATED': False}

In [44]:
# androidLog
androidLog = [log for log in rlog_list if log.which() == "androidLog"]
androidLog[0].androidLog.to_dict()

{'id': 0,
 'ts': 1705234287979967,
 'priority': 3,
 'pid': 0,
 'tid': 0,
 'message': '{"MESSAGE": "[thermald] engaged: False", "PRIORITY": "3", "SYSLOG_FACILITY": "1", "_BOOT_ID": "c7e745cbf6814793891015b761350a24", "_HOSTNAME": "tici", "_MACHINE_ID": "0e56b517e1dbc6ffa9481f7263f690e5", "_SOURCE_MONOTONIC_TIMESTAMP": "1151021261", "_TRANSPORT": "kernel"}'}

In [45]:
# cameraOdometry
cameraOdometry = [log for log in rlog_list if log.which() == "cameraOdometry"]
cameraOdometry[0].cameraOdometry.to_dict()

{'trans': [13.009315490722656, 0.09612151235342026, 0.026201508939266205],
 'rot': [-0.0009666606783866882, 0.020906340330839157, 0.016553644090890884],
 'transStd': [0.3503006398677826, 0.042587652802467346, 0.02921556495130062],
 'rotStd': [0.005170276388525963, 0.003795625874772668, 0.0016031470149755478],
 'frameId': 12002,
 'timestampEof': 1150954576278,
 'wideFromDeviceEuler': [2.68887379206717e-06,
  0.016017800197005272,
  -0.006828834302723408],
 'wideFromDeviceEulerStd': [0.0010494886664673686,
  0.002135524293407798,
  0.0035245714243501425],
 'roadTransformTrans': [1.8873834051191807e-08,
  -4.5303022488951683e-07,
  1.374474048614502],
 'roadTransformTransStd': [0.0009847639594227076,
  0.0009845010936260223,
  0.030580539256334305]}

In [46]:
# can
can = [log for log in rlog_list if log.which() == "can"]
can[0].to_dict()

{'can': [{'address': 1864,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 1865,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 1866,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 1867,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 897,
   'busTime': 0,
   'dat': b'\x80\x88@\x00\x00\x91\xde\x05',
   'src': 0},
  {'address': 897,
   'busTime': 0,
   'dat': b'\x80\x88@\x00\x00\x91\xde\x05',
   'src': 2},
  {'address': 1868,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 593,
   'busTime': 0,
   'dat': b'\x15\x04"\xa2\x00\x10\xd8\x7f',
   'src': 0},
  {'address': 593,
   'busTime': 0,
   'dat': b'\x15\x04"\xa2\x00\x10\xd8\x7f',
   'src': 2},
  {'address': 1869,
   'busTime': 0,
   'dat': b'\x00\x00\x00\x00\x00\x00\x90\xe9',
   'src': 1},
  {'address': 688, 'busTime':

In [47]:
# carControl
carControl = [log for log in rlog_list if log.which() == "carControl"]
carControl[0].carControl.to_dict()

{'enabled': False,
 'gasDEPRECATED': 0.0,
 'brakeDEPRECATED': 0.0,
 'steeringTorqueDEPRECATED': 0.0,
 'cruiseControl': {'cancel': False,
  'resume': False,
  'speedOverrideDEPRECATED': 0.0,
  'accelOverrideDEPRECATED': 0.0,
  'override': False},
 'hudControl': {'speedVisible': False,
  'setSpeed': 70.83333587646484,
  'lanesVisible': False,
  'leadVisible': False,
  'visualAlert': 'none',
  'audibleAlert': 'none',
  'rightLaneVisible': True,
  'leftLaneVisible': True,
  'rightLaneDepart': False,
  'leftLaneDepart': False},
 'actuators': {'gas': 0.0,
  'brake': 0.0,
  'steer': 0.0,
  'steeringAngleDeg': -0.017548255622386932,
  'accel': 0.0,
  'longControlState': 'off',
  'speed': 0.0,
  'curvature': 0.0016474168514832854,
  'steerOutputCan': 0.0},
 'activeDEPRECATED': False,
 'rollDEPRECATED': 0.0,
 'pitchDEPRECATED': 0.0,
 'latActive': False,
 'longActive': False,
 'orientationNED': [0.0909862145781517,
  0.009810217656195164,
  0.2974139153957367],
 'angularVelocity': [0.001237853779

In [48]:
# carParams
carParams = [log for log in rlog_list if log.which() == "carParams"]
carParams[0].carParams.to_dict()

{'carName': 'mock',
 'carFingerprint': 'mock',
 'enableGasInterceptor': False,
 'pcmCruise': True,
 'enableCameraDEPRECATED': False,
 'enableDsu': False,
 'enableApgsDEPRECATED': False,
 'minEnableSpeed': -1.0,
 'minSteerSpeed': 0.0,
 'safetyModelDEPRECATED': 'silent',
 'safetyParamDEPRECATED': 0,
 'mass': 1836.0,
 'wheelbase': 2.700000047683716,
 'centerToFront': 1.350000023841858,
 'steerRatio': 13.0,
 'steerRatioRear': 0.0,
 'rotationalInertia': 3139.534912109375,
 'tireStiffnessFront': 201087.203125,
 'tireStiffnessRear': 317877.90625,
 'longitudinalTuning': {'kpBP': [0.0],
  'kpV': [1.0],
  'kiBP': [0.0],
  'kiV': [1.0],
  'deadzoneBP': [0.0],
  'deadzoneV': [0.0],
  'kf': 1.0},
 'lateralTuning': {'pid': {'kf': 0.0}},
 'steerLimitAlert': False,
 'vEgoStopping': 0.5,
 'directAccelControlDEPRECATED': False,
 'stoppingControl': True,
 'startAccel': 0.0,
 'steerRateCostDEPRECATED': 0.0,
 'steerControlType': 'torque',
 'radarUnavailable': False,
 'steerActuatorDelay': 0.0,
 'openpilotL

In [49]:
# carState
carState = [log for log in rlog_list if log.which() == "carState"]
carState[0].carState.to_dict()

{'vEgo': 11.123780250549316,
 'gas': 0.0,
 'gasPressed': False,
 'brake': 0.0,
 'brakePressed': False,
 'steeringAngleDeg': 0.0,
 'steeringTorque': 0.0,
 'steeringPressed': False,
 'cruiseState': {'enabled': False,
  'speed': 0.0,
  'available': False,
  'speedOffset': 0.0,
  'standstill': False,
  'nonAdaptive': False,
  'speedCluster': 0.0},
 'events': [{'name': 'carUnrecognized',
   'enable': False,
   'noEntry': False,
   'warning': False,
   'userDisable': False,
   'softDisable': False,
   'immediateDisable': False,
   'preEnable': False,
   'permanent': True,
   'overrideLongitudinal': False,
   'overrideLateral': False}],
 'gearShifter': 'unknown',
 'steeringRateDeg': 0.0,
 'aEgo': 0.0,
 'vEgoRaw': 11.123780250549316,
 'standstill': False,
 'brakeLightsDEPRECATED': False,
 'leftBlinker': False,
 'rightBlinker': False,
 'yawRate': 0.0,
 'genericToggle': False,
 'doorOpen': False,
 'seatbeltUnlatched': False,
 'canValid': True,
 'steeringTorqueEps': 0.0,
 'clutchPressed': False,


In [50]:
# controlsState
controlsState = [log for log in rlog_list if log.which() == "controlsState"]
controlsState[0].controlsState.to_dict()

{'vEgoDEPRECATED': 0.0,
 'aEgoDEPRECATED': 0.0,
 'vPid': 11.123780250549316,
 'vTargetLead': 0.0,
 'upAccelCmd': 0.0,
 'uiAccelCmd': 0.0,
 'yActualDEPRECATED': 0.0,
 'yDesDEPRECATED': 0.0,
 'upSteerDEPRECATED': 0.0,
 'uiSteerDEPRECATED': 0.0,
 'aTargetMinDEPRECATED': 0.0,
 'aTargetMaxDEPRECATED': 0.0,
 'jerkFactorDEPRECATED': 0.0,
 'angleSteersDEPRECATED': 0.0,
 'hudLeadDEPRECATED': 0,
 'cumLagMs': -8.586008071899414,
 'canMonoTimeDEPRECATED': 0,
 'radarStateMonoTimeDEPRECATED': 0,
 'mdMonoTimeDEPRECATED': 0,
 'enabled': False,
 'steerOverrideDEPRECATED': False,
 'vCruise': 255.0,
 'rearViewCamDEPRECATED': False,
 'alertText1': 'Dashcam Mode',
 'alertText2': 'Car Unrecognized',
 'awarenessStatusDEPRECATED': 0.0,
 'angleModelBiasDEPRECATED': 0.0,
 'longitudinalPlanMonoTime': 1150947766017,
 'steeringAngleDesiredDegDEPRECATED': 0.0,
 'longControlState': 'off',
 'state': 'disabled',
 'vEgoRawDEPRECATED': 0.0,
 'ufAccelCmd': 0.0,
 'ufSteerDEPRECATED': 0.0,
 'aTarget': 0.0,
 'active': False

In [51]:
# deviceState
deviceState = [log for log in rlog_list if log.which() == "deviceState"]
deviceState[0].deviceState.to_dict()

{'cpu0DEPRECATED': 0,
 'cpu1DEPRECATED': 0,
 'cpu2DEPRECATED': 0,
 'cpu3DEPRECATED': 0,
 'memDEPRECATED': 0,
 'gpuDEPRECATED': 0,
 'batDEPRECATED': 0,
 'freeSpacePercent': 63.71802520751953,
 'batteryPercentDEPRECATED': 0,
 'fanSpeedPercentDesired': 30,
 'started': True,
 'usbOnlineDEPRECATED': False,
 'startedMonoTime': 549157996143,
 'thermalStatus': 'green',
 'batteryCurrentDEPRECATED': 0,
 'batteryVoltageDEPRECATED': 0,
 'chargingErrorDEPRECATED': False,
 'chargingDisabledDEPRECATED': False,
 'memoryUsagePercent': 54,
 'cpuUsagePercentDEPRECATED': 0,
 'pa0DEPRECATED': 0,
 'networkType': 'none',
 'offroadPowerUsageUwh': 0,
 'networkStrength': 'unknown',
 'carBatteryCapacityUwh': 30006284,
 'cpuTempC': [68.30000305175781,
  68.0,
  68.0,
  67.30000305175781,
  67.5999984741211,
  65.69999694824219,
  67.30000305175781,
  67.30000305175781],
 'gpuTempC': [71.19999694824219, 68.5999984741211],
 'memoryTempC': 62.900001525878906,
 'batteryTempCDEPRECATED': 0.0,
 'ambientTempC': 55.25400

In [52]:
# driverCameraState
driverCameraState = [log for log in rlog_list if log.which() == "driverCameraState"]
driverCameraState[0].driverCameraState.to_dict()

{'frameId': 12002,
 'encodeId': 0,
 'timestampEof': 1150955149715,
 'frameLengthDEPRECATED': 0,
 'integLines': 924,
 'globalGainDEPRECATED': 0,
 'frameType': 'front',
 'timestampSof': 1150940320288,
 'lensPosDEPRECATED': 0,
 'lensSagDEPRECATED': 0.0,
 'lensErrDEPRECATED': 0.0,
 'lensTruePosDEPRECATED': 0.0,
 'gain': 11.4375,
 'recoverStateDEPRECATED': 0,
 'highConversionGain': True,
 'measuredGreyFraction': 0.23828125,
 'targetGreyFraction': 0.23404505848884583,
 'processingTime': 0.014691406860947609,
 'frameIdSensor': 0,
 'sensor': 'ox03c10',
 'exposureValPercent': 4.5890421867370605,
 'requestId': 0}

In [53]:
# driverEncodeIdx
driverEncodeIdx = [log for log in rlog_list if log.which() == "driverEncodeIdx"]
driverEncodeIdx[0].driverEncodeIdx.to_dict()

{'frameId': 12002,
 'type': 'fullHEVC',
 'encodeId': 12000,
 'segmentNum': 10,
 'segmentId': 0,
 'segmentIdEncode': 0,
 'timestampSof': 1150940320288,
 'timestampEof': 1150955149715,
 'flags': 2147500040,
 'len': 81076}

In [54]:
# driverMonitoringState
driverMonitoringState = [log for log in rlog_list if log.which() == "driverMonitoringState"]
driverMonitoringState[6].driverMonitoringState.to_dict()

{'events': [],
 'faceDetected': True,
 'isDistracted': False,
 'awarenessStatus': 1.0,
 'isRHD': False,
 'rhdCheckedDEPRECATED': False,
 'posePitchOffset': -0.16098178923130035,
 'posePitchValidCount': 1108,
 'poseYawOffset': 0.009593985974788666,
 'poseYawValidCount': 919,
 'stepChange': 0.004545454401522875,
 'awarenessActive': 1.0,
 'awarenessPassive': 1.0,
 'isLowStd': True,
 'hiStdCount': 0,
 'isPreviewDEPRECATED': False,
 'isActiveMode': True,
 'distractedType': 0}

In [55]:
# driverStateV2
driverMonitoringState = [log for log in rlog_list if log.which() == "driverStateV2"]
driverMonitoringState[0].driverStateV2.to_dict()


{'frameId': 12002,
 'modelExecutionTime': 0.02009500004351139,
 'dspExecutionTime': 0.018908072263002396,
 'rawPredictions': b'',
 'poorVisionProb': 0.0009536235593259335,
 'wheelOnRightProb': 0.0009536235593259335,
 'leftDriverData': {'faceOrientation': [0.012783616781234741,
   0.4985610544681549,
   0.0639180839061737],
  'faceOrientationStd': [0.036017853766679764,
   0.030895529314875603,
   0.021599499508738518],
  'facePosition': [0.14061978459358215, -0.025567233562469482],
  'facePositionStd': [0.0029400477651506662, 0.0034274945501238108],
  'faceProb': 0.9533332586288452,
  'leftEyeProb': 0.9900688529014587,
  'rightEyeProb': 0.8905638456344604,
  'leftBlinkProb': 0.06543692946434021,
  'rightBlinkProb': 0.06543692946434021,
  'sunglassesProb': 0.0009536235593259335,
  'occludedProb': 0.4872191548347473,
  'readyProb': [0.5509569048881531,
   0.4744550287723541,
   0.5635721683502197,
   0.4872191548347473],
  'notReadyProb': [0.016451386734843254, 0.0009061292512342334]},
 

In [56]:
# gpsLocation
gpsLocation = [log for log in rlog_list if log.which() == "gpsLocation"]
gpsLocation[0].gpsLocation.to_dict()

{'flags': 1,
 'latitude': 63.33374455419531,
 'longitude': 10.357024841927617,
 'altitude': 181.32598876953125,
 'speed': 12.090862274169922,
 'bearingDeg': 18.020095825195312,
 'accuracy': 0.0,
 'unixTimestampMillis': 1705234288404,
 'source': 'qcomdiag',
 'vNED': [11.497502326965332, 3.7402238845825195, 0.08433574438095093],
 'verticalAccuracy': 0.999218225479126,
 'bearingAccuracyDeg': 0.34702321887016296,
 'speedAccuracy': 0.11579705774784088}

In [57]:
# gyroscope
gyroscope = [log for log in rlog_list if log.which() == "gyroscope"]
gyroscope[0].gyroscope.to_dict()

{'gyroUncalibrated': {'v': [-0.022449297830462456,
   -0.05390885844826698,
   0.0044287727214396],
  'status': 1},
 'version': 2,
 'sensor': 5,
 'type': 16,
 'timestamp': 1150993498933,
 'source': 'lsm6ds3trc',
 'uncalibratedDEPRECATED': False}

In [58]:
# initData
initData = [log for log in rlog_list if log.which() == "initData"]
initData[0].initData.to_dict()


{'kernelArgs': ['rcupdate.rcu_expedited=1',
  'console=ttyMSM0,115200n8',
  'quiet',
  'loglevel=3',
  'earlycon=msm_geni_serial,0xA84000',
  'androidboot.hardware=qcom',
  'androidboot.console=ttyMSM0',
  'video=DSI-1:1080x2160@60e',
  'ehci-hcd.park=3',
  'lpm_levels.sleep_disabled=1',
  'service_locator.enable=1',
  'androidboot.selinux=permissive',
  'firmware_class.path=/lib/firmware/updates',
  'net.ifnames=0',
  'dyndbg=""',
  'root=/dev/sda6',
  'androidboot.bootdevice=1d84000.ufshc',
  'androidboot.serialno=9e856db5',
  'androidboot.baseband=sda',
  'msm_drm.dsi_display0=dsi_fhd_ea8074_1080_cmd_display:',
  'androidboot.slot_suffix=_a',
  'skip_initramfs',
  'rootwait',
  'ro',
  'init=/sbin/init'],
 'dongleId': '45ba82b7ecf23784',
 'deviceType': 'tizi',
 'version': '0.9.5-release',
 'dirty': False,
 'gitCommit': '0df64642759d61f59cc6f09b598ddadb7df96459',
 'gitBranch': 'release3',
 'passive': False,
 'gitRemote': 'https://github.com/commaai/openpilot.git',
 'kernelVersion': '

In [59]:
# lateralPlanDEPRECATED
lateralPlanDEPRECATED = [log for log in rlog_list if log.which() == "lateralPlanDEPRECATED"]
lateralPlanDEPRECATED[0].lateralPlanDEPRECATED.to_dict()

{'laneWidthDEPRECATED': 0.0,
 'cProbDEPRECATED': 0.0,
 'lProbDEPRECATED': 0.0,
 'rProbDEPRECATED': 0.0,
 'steeringAngleDegDEPRECATED': 0.0,
 'mpcSolutionValid': True,
 'paramsValidDEPRECATED': False,
 'angleOffsetDegDEPRECATED': 0.0,
 'modelValidDEPRECATED': False,
 'steeringRateDegDEPRECATED': 0.0,
 'sensorValidDEPRECATED': False,
 'commIssueDEPRECATED': False,
 'posenetValidDEPRECATED': False,
 'desire': 'none',
 'laneChangeState': 'off',
 'laneChangeDirection': 'none',
 'dPathPoints': [-0.19102370738983154,
  -0.1900283396244049,
  -0.18813884258270264,
  -0.18338993191719055,
  -0.17702734470367432,
  -0.16312259435653687,
  -0.14615926146507263,
  -0.11774803698062897,
  -0.07740622758865356,
  -0.023734692484140396,
  0.04923996329307556,
  0.14366000890731812,
  0.26335519552230835,
  0.41001248359680176,
  0.5871993899345398,
  0.8013900518417358,
  1.050004243850708,
  1.3452321290969849,
  1.687171220779419,
  2.0863122940063477,
  2.5408852100372314,
  3.0675089359283447,
  

In [60]:
# liveCalibration
liveCalibration = [log for log in rlog_list if log.which() == "liveCalibration"]
liveCalibration[0].liveCalibration.to_dict()

{'calStatusDEPRECATED': 0,
 'calCycle': 0,
 'calPerc': 100,
 'rpyCalib': [-3.4374086681054905e-05,
  0.07334545999765396,
  -0.012159438803792],
 'rpyCalibSpread': [0.0007780042942613363,
  0.0035418143961578608,
  0.010637844912707806],
 'validBlocks': 50,
 'wideFromDeviceEuler': [2.5382785224792315e-06,
  0.012765408493578434,
  -0.010278177447617054],
 'calStatus': 'calibrated',
 'height': [1.3572218418121338]}

In [61]:
# liveLocationKalman
liveLocationKalman = [log for log in rlog_list if log.which() == "liveLocationKalman"]
liveLocationKalman[0].liveLocationKalman.to_dict()

{'positionECEF': {'value': [2823457.5734663,
   516012.1733844021,
   5676937.590571662],
  'std': [1.2323829950692442, 0.9752153284271723, 0.7224659874361306],
  'valid': True},
 'positionGeodetic': {'value': [63.333783251923734,
   10.357015623552735,
   185.134004195134],
  'std': [nan, nan, nan],
  'valid': True},
 'velocityECEF': {'value': [-10.908992512496493,
   1.7291359728622242,
   5.3789588606932295],
  'std': [0.3222951494882218, 0.1675747437476186, 0.11392075651915391],
  'valid': True},
 'velocityNED': {'value': [11.726068608740679,
   3.6621832398680714,
   -0.13021588115233929],
  'std': [nan, nan, nan],
  'valid': True},
 'velocityDevice': {'value': [12.251733308120023,
   -0.09470985576657198,
   -0.9029331455340235],
  'std': [0.3294108664506319, 0.12019431421447062, 0.16924035168813495],
  'valid': True},
 'accelerationDevice': {'value': [0.9910625072649084,
   -0.15271801346960082,
   -0.11595466434476684],
  'std': [0.42872616159508914, 0.4259198312852751, 0.42322

In [62]:
# liveParameters
liveParameters = [log for log in rlog_list if log.which() == "liveParameters"]
liveParameters[0].liveParameters.to_dict()

{'valid': False,
 'gyroBias': 0.0,
 'angleOffsetDeg': 0.0004382760089356452,
 'angleOffsetAverageDeg': -0.016000723466277122,
 'stiffnessFactor': 0.8530488014221191,
 'steerRatio': 0.0027772290632128716,
 'sensorValid': True,
 'yawRateDEPRECATED': 0.0,
 'posenetSpeed': 0.0,
 'posenetValid': True,
 'angleOffsetFastStd': 0.0038429826963692904,
 'angleOffsetAverageStd': 0.0036947806365787983,
 'stiffnessFactorStd': 0.007423726376146078,
 'steerRatioStd': 0.04479100555181503,
 'roll': 0.0896860808134079}

In [63]:
# liveTorqueParameters
liveTorqueParameters = [log for log in rlog_list if log.which() == "liveTorqueParameters"]
liveTorqueParameters[0].liveTorqueParameters.to_dict()

{'liveValid': False,
 'latAccelFactorRaw': 0.0,
 'latAccelOffsetRaw': 0.0,
 'frictionCoefficientRaw': 0.0,
 'latAccelFactorFiltered': 0.0,
 'latAccelOffsetFiltered': 0.0,
 'frictionCoefficientFiltered': 0.0,
 'totalBucketPoints': 0.0,
 'decay': 50.0,
 'maxResets': 1.0,
 'version': 1,
 'useParams': False}

In [64]:
# liveTracks
liveTracks = [log for log in rlog_list if log.which() == "liveTracks"]
liveTracks[5].liveTracks

<capnp list reader []>

In [65]:
# logMessage
logMessage = [log for log in rlog_list if log.which() == "logMessage"]
logMessage[0].logMessage

'{"created": 1705234287.9445829, "ctx": {"daemon": "loggerd", "device": "tizi", "dirty": false, "dongle_id": "45ba82b7ecf23784", "version": "0.9.5-release"}, "filename": "system/loggerd/loggerd.cc", "funcname": "handle_encoder_msg", "levelnum": 10, "lineno": 164, "msg": "rotate 9 -> 10 ready 4/4 for driverEncodeData"}'

In [66]:
# longitudinalPlan
longitudinalPlan = [log for log in rlog_list if log.which() == "longitudinalPlan"]
longitudinalPlan[0].longitudinalPlan.to_dict()


{'lateralValidDEPRECATED': False,
 'longitudinalValidDEPRECATED': False,
 'vTargetDEPRECATED': 0.0,
 'aTargetMinDEPRECATED': 0.0,
 'aTargetMaxDEPRECATED': 0.0,
 'jerkFactorDEPRECATED': 0.0,
 'hasLead': False,
 'fcw': False,
 'modelMonoTime': 1150991370861,
 'radarStateMonoTimeDEPRECATED': 0,
 'laneWidthDEPRECATED': 0.0,
 'vTargetFutureDEPRECATED': 0.0,
 'longitudinalPlanSource': 'cruise',
 'vCruiseDEPRECATED': 0.0,
 'aCruiseDEPRECATED': 0.0,
 'aTargetDEPRECATED': 0.0,
 'gpsPlannerActiveDEPRECATED': False,
 'vMaxDEPRECATED': 0.0,
 'vCurvatureDEPRECATED': 0.0,
 'decelForTurnDEPRECATED': False,
 'hasLeftLaneDEPRECATED': False,
 'hasRightLaneDEPRECATED': False,
 'mapValidDEPRECATED': False,
 'vStartDEPRECATED': 0.0,
 'aStartDEPRECATED': 0.0,
 'radarValidDEPRECATED': False,
 'processingDelay': -1150991335424.0,
 'radarCanErrorDEPRECATED': False,
 'commIssueDEPRECATED': False,
 'accels': [0.0,
  0.018111838027834892,
  0.07244735211133957,
  0.15897506475448608,
  0.27081772685050964,
  0.41

In [67]:
# magnetometer
magnetometer = [log for log in rlog_list if log.which() == "magnetometer"]
magnetometer[0].magnetometer.to_dict()

{'magneticUncalibrated': {'v': [-0.17822265625,
   0.05474853515625,
   0.27471923828125,
   -0.13311767578125,
   -1.10430908203125,
   0.88885498046875],
  'status': 1},
 'version': 1,
 'sensor': 3,
 'type': 14,
 'timestamp': 1150979917215,
 'source': 'mmc5603nj',
 'uncalibratedDEPRECATED': False}

In [68]:
# managerState
managerState = [log for log in rlog_list if log.which() == "managerState"]
managerState[0].managerState.to_dict()

{'processes': [{'name': 'manage_athenad',
   'pid': 0,
   'running': False,
   'exitCode': 0,
   'shouldBeRunning': False},
  {'name': 'camerad',
   'pid': 49081,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'logcatd',
   'pid': 49083,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'proclogd',
   'pid': 49084,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'logmessaged',
   'pid': 37268,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'micd',
   'pid': 49085,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'timezoned',
   'pid': 37310,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'dmonitoringmodeld',
   'pid': 49088,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 'encoderd',
   'pid': 49092,
   'running': True,
   'exitCode': 0,
   'shouldBeRunning': True},
  {'name': 's

In [69]:
# mapRenderState
mapRenderState = [log for log in rlog_list if log.which() == "mapRenderState"]
mapRenderState[0].mapRenderState.to_dict()

{'locationMonoTime': 1151243620340, 'renderTime': 0.0, 'frameId': 1199}

In [70]:
# microphone
microphone = [log for log in rlog_list if log.which() == "microphone"]
microphone[0].microphone.to_dict()

{'soundPressure': 0.1452663689851761,
 'soundPressureWeightedDb': 41.63510513305664,
 'filteredSoundPressureWeightedDb': 41.42350769042969,
 'soundPressureWeighted': 0.0024142665788531303}

In [71]:
# modelV2
modelV2 = [log for log in rlog_list if log.which() == "modelV2"]
modelV2[0].modelV2.to_dict()


{'frameId': 12002,
 'frameAge': 0,
 'frameDropPerc': 0.0,
 'timestampEof': 1150954576278,
 'position': {'x': [-0.8604580163955688,
   -0.7412617802619934,
   -0.3716745972633362,
   0.2560199499130249,
   1.151122808456421,
   2.305532693862915,
   3.724886417388916,
   5.4117326736450195,
   7.390104293823242,
   9.639155387878418,
   12.182552337646484,
   15.031630516052246,
   18.173446655273438,
   21.63915252685547,
   25.4178466796875,
   29.537952423095703,
   33.97010803222656,
   38.75246047973633,
   43.88572692871094,
   49.447383880615234,
   55.29431915283203,
   61.53337097167969,
   68.14047241210938,
   75.15754699707031,
   82.60723114013672,
   90.40782165527344,
   98.68488311767578,
   107.48927307128906,
   116.56349182128906,
   126.20108032226562,
   136.26803588867188,
   146.7908172607422,
   157.74130249023438],
  'y': [-0.19102370738983154,
   -0.1900283396244049,
   -0.18813884258270264,
   -0.18338993191719055,
   -0.17702734470367432,
   -0.16312259435653

In [72]:
# navInstruction
navInstruction = [log for log in rlog_list if log.which() == "navInstruction"]
navInstruction[0].navInstruction.to_dict()

{'maneuverDistance': 0.0,
 'distanceRemaining': 0.0,
 'timeRemaining': 0.0,
 'timeRemainingTypical': 0.0,
 'showFull': False,
 'speedLimit': 0.0,
 'speedLimitSign': 'mutcd'}

In [73]:
# navModel
navModel = [log for log in rlog_list if log.which() == "navModel"]
navModel[0].navModel.to_dict()

{'frameId': 1199,
 'modelExecutionTime': 0.007820416241884232,
 'dspExecutionTime': 0.0077092708088457584,
 'features': [0.7999680638313293,
  0.4756566882133484,
  0.5513293147087097,
  0.5080878138542175,
  0.45944109559059143,
  0.4972774386405945,
  0.3837684392929077,
  0.5891656279563904,
  0.5675448775291443,
  0.5945708155632019,
  0.5513293147087097,
  0.30269062519073486,
  0.1891816258430481,
  0.3891736567020416,
  0.2378283441066742,
  0.3405269384384155,
  0.32431137561798096,
  0.39457884430885315,
  0.4540359079837799,
  0.4756566882133484,
  0.3999840319156647,
  0.3783632516860962,
  0.43782034516334534,
  0.3891736567020416,
  0.3135010004043579,
  0.5459241271018982,
  0.23242314159870148,
  0.5243033766746521,
  0.44322553277015686,
  0.4810618758201599,
  0.6161916255950928,
  0.5080878138542175,
  0.5513293147087097,
  0.4324151575565338,
  0.4702514708042145,
  0.5675448775291443,
  0.29188022017478943,
  0.5621396899223328,
  0.21080239117145538,
  0.4648462831

In [74]:
# navThumbnail
navThumbnail = [log for log in rlog_list if log.which() == "navThumbnail"]
navThumbnail[0].navThumbnail.to_dict()

{'frameId': 1200,
 'timestampEof': 1151791629975,
 'thumbnail': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x01\x00d\x00d\x00\x00\xff\xdb\x00C\x00\x10\x0b\x0c\x0e\x0c\n\x10\x0e\r\x0e\x12\x11\x10\x13\x18(\x1a\x18\x16\x16\x181#%\x1d(:3=<9387@H\\N@DWE78PmQW_bghg>Mqypdx\\egc\xff\xdb\x00C\x01\x11\x12\x12\x18\x15\x18/\x1a\x1a/cB8Bcccccccccccccccccccccccccccccccccccccccccccccccccc\xff\xc0\x00\x11\x08\x01\x00\x01\x00\x03\x01"\x00\x02\x11\x01\x03\x11\x01\xff\xc4\x00\x1f\x00\x00\x01\x05\x01\x01\x01\x01\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x01\x02\x03\x04\x05\x06\x07\x08\t\n\x0b\xff\xc4\x00\xb5\x10\x00\x02\x01\x03\x03\x02\x04\x03\x05\x05\x04\x04\x00\x00\x01}\x01\x02\x03\x00\x04\x11\x05\x12!1A\x06\x13Qa\x07"q\x142\x81\x91\xa1\x08#B\xb1\xc1\x15R\xd1\xf0$3br\x82\t\n\x16\x17\x18\x19\x1a%&\'()*456789:CDEFGHIJSTUVWXYZcdefghijstuvwxyz\x83\x84\x85\x86\x87\x88\x89\x8a\x92\x93\x94\x95\x96\x97\x98\x99\x9a\xa2\xa3\xa4\xa5\xa6\xa7\xa8\xa9\xaa\xb2\xb3\xb4\xb5\xb6\xb7\xb8\xb9\xba\xc2\xc3\xc4\xc5\xc6\xc7\xc8\x

In [75]:
# onroadEvents
onroadEvents = [log for log in rlog_list if log.which() == "onroadEvents"]
onroadEvents[0].onroadEvents[0].to_dict()

{'name': 'carUnrecognized',
 'enable': False,
 'noEntry': False,
 'warning': False,
 'userDisable': False,
 'softDisable': False,
 'immediateDisable': False,
 'preEnable': False,
 'permanent': True,
 'overrideLongitudinal': False,
 'overrideLateral': False}

In [76]:
# pandaStates
pandaStates = [log for log in rlog_list if log.which() == "pandaStates"]
pandaStates[0].pandaStates[0].to_dict()

{'voltage': 13937,
 'current': 0,
 'ignitionLine': True,
 'controlsAllowed': False,
 'gasInterceptorDetectedDEPRECATED': False,
 'startedSignalDetectedDEPRECATED': False,
 'hasGpsDEPRECATED': False,
 'rxBufferOverflow': 0,
 'txBufferOverflow': 0,
 'gmlanSendErrs': 0,
 'pandaType': 'tres',
 'fanSpeedRpmDEPRECATED': 0,
 'usbPowerModeDEPRECATED': 'none',
 'ignitionCan': False,
 'safetyModel': 'noOutput',
 'faultStatus': 'none',
 'powerSaveEnabled': False,
 'uptime': 1129,
 'faults': [],
 'safetyRxInvalid': 0,
 'safetyParamDEPRECATED': 0,
 'harnessStatus': 'normal',
 'heartbeatLost': False,
 'alternativeExperience': 1,
 'safetyTxBlocked': 0,
 'interruptLoad': 0.12014320492744446,
 'safetyParam2DEPRECATED': 0,
 'safetyParam': 0,
 'fanPower': 26,
 'canState0': {'busOff': False,
  'busOffCnt': 0,
  'errorWarning': False,
  'errorPassive': False,
  'lastError': 'noError',
  'lastStoredError': 'stuffError',
  'lastDataError': 'noChange',
  'lastDataStoredError': 'noError',
  'receiveErrorCnt': 

In [77]:
# peripheralState
peripheralState = [log for log in rlog_list if log.which() == "peripheralState"]
peripheralState[0].peripheralState.to_dict()

{'pandaType': 'tres',
 'voltage': 14089,
 'current': 728,
 'fanSpeedRpm': 1985,
 'usbPowerModeDEPRECATED': 'none'}

In [78]:
# procLog
procLog = [log for log in rlog_list if log.which() == "procLog"]
procLog[0].procLog.to_dict()

{'cpuTimes': [{'cpuNum': 0,
   'user': 257.0,
   'nice': 0.009999999776482582,
   'system': 171.25,
   'idle': 651.8599853515625,
   'iowait': 0.7300000190734863,
   'irq': 18.600000381469727,
   'softirq': 6.130000114440918},
  {'cpuNum': 1,
   'user': 200.3800048828125,
   'nice': 0.019999999552965164,
   'system': 183.3699951171875,
   'idle': 642.7100219726562,
   'iowait': 0.9800000190734863,
   'irq': 51.130001068115234,
   'softirq': 3.930000066757202},
  {'cpuNum': 2,
   'user': 226.72000122070312,
   'nice': 0.029999999329447746,
   'system': 116.62000274658203,
   'idle': 755.5900268554688,
   'iowait': 0.8299999833106995,
   'irq': 5.869999885559082,
   'softirq': 2.9600000381469727},
  {'cpuNum': 3,
   'user': 164.8300018310547,
   'nice': 0.0,
   'system': 225.97999572753906,
   'idle': 711.1199951171875,
   'iowait': 0.6800000071525574,
   'irq': 4.96999979019165,
   'softirq': 3.009999990463257},
  {'cpuNum': 4,
   'user': 284.239990234375,
   'nice': 0.02999999932944774

In [79]:
# qRoadEncodeIdx
qRoadEncodeIdx = [log for log in rlog_list if log.which() == "qRoadEncodeIdx"]
qRoadEncodeIdx[0].qRoadEncodeIdx.to_dict()

{'frameId': 12002,
 'type': 'qcameraH264',
 'encodeId': 12000,
 'segmentNum': 10,
 'segmentId': 0,
 'segmentIdEncode': 0,
 'timestampSof': 1150939854090,
 'timestampEof': 1150954576278,
 'flags': 2147500040,
 'len': 2416}

In [81]:
# qcomGnss
qcomGnss = [log for log in rlog_list if log.which() == "qcomGnss"]
qcomGnss[0].qcomGnss.to_dict()

{'measurementReport': {'source': 'glonass',
  'fCount': 1091820,
  'gpsWeek': 0,
  'glonassCycleNumber': 8,
  'glonassNumberOfDays': 14,
  'milliseconds': 54688404,
  'timeBias': -0.15704241394996643,
  'clockTimeUncertainty': 29.224851608276367,
  'clockFrequencyBias': 0.7058225274085999,
  'clockFrequencyUncertainty': 3.144987106323242,
  'sv': [{'svId': 74,
    'glonassFrequencyIndex': -7,
    'observationState': 'track',
    'observations': 45,
    'goodObservations': 45,
    'gpsParityErrorCount': 0,
    'glonassHemmingErrorCount': 1,
    'filterStages': 1,
    'carrierNoise': 2190,
    'latency': 11,
    'predetectInterval': 20,
    'postdetections': 46,
    'unfilteredMeasurementIntegral': 54688319,
    'unfilteredMeasurementFraction': 0.5866732597351074,
    'unfilteredTimeUncertainty': 0.0004871703567914665,
    'unfilteredSpeed': 695.3018188476562,
    'unfilteredSpeedUncertainty': 0.8299999833106995,
    'measurementStatus': {'subMillisecondIsValid': True,
     'subBitTimeIs

In [82]:
# radarState
radarState = [log for log in rlog_list if log.which() == "radarState"]
radarState[0].radarState.to_dict()


{'angleOffsetDEPRECATED': 0.0,
 'calStatusDEPRECATED': 0,
 'leadOne': {'dRel': 0.0,
  'yRel': 0.0,
  'vRel': 0.0,
  'aRel': 0.0,
  'vLead': 0.0,
  'aLeadDEPRECATED': 0.0,
  'dPath': 0.0,
  'vLat': 0.0,
  'vLeadK': 0.0,
  'aLeadK': 0.0,
  'fcw': False,
  'status': False,
  'aLeadTau': 0.0,
  'modelProb': 0.0,
  'radar': False,
  'radarTrackId': -1},
 'leadTwo': {'dRel': 0.0,
  'yRel': 0.0,
  'vRel': 0.0,
  'aRel': 0.0,
  'vLead': 0.0,
  'aLeadDEPRECATED': 0.0,
  'dPath': 0.0,
  'vLat': 0.0,
  'vLeadK': 0.0,
  'aLeadK': 0.0,
  'fcw': False,
  'status': False,
  'aLeadTau': 0.0,
  'modelProb': 0.0,
  'radar': False,
  'radarTrackId': -1},
 'cumLagMs': 9449.42578125,
 'mdMonoTime': 1150991370861,
 'ftMonoTimeDEPRECATED': 0,
 'calCycleDEPRECATED': 0,
 'calPercDEPRECATED': 0,
 'carStateMonoTime': 1151004386799,
 'radarErrors': []}

In [83]:
# roadCameraState
roadCameraState = [log for log in rlog_list if log.which() == "roadCameraState"]
roadCameraState[0].roadCameraState.to_dict()

{'frameId': 12003,
 'encodeId': 0,
 'timestampEof': 1151004571538,
 'frameLengthDEPRECATED': 0,
 'integLines': 131,
 'globalGainDEPRECATED': 0,
 'frameType': 'unknown',
 'timestampSof': 1150989854299,
 'lensPosDEPRECATED': 0,
 'lensSagDEPRECATED': 0.0,
 'lensErrDEPRECATED': 0.0,
 'lensTruePosDEPRECATED': 0.0,
 'gain': 7.320000171661377,
 'recoverStateDEPRECATED': 0,
 'highConversionGain': True,
 'measuredGreyFraction': 0.31640625,
 'targetGreyFraction': 0.31186723709106445,
 'processingTime': 0.005904478952288628,
 'frameIdSensor': 0,
 'sensor': 'ox03c10',
 'exposureValPercent': 0.4211210310459137,
 'requestId': 0}

In [84]:
# roadEncodeIdx
roadEncodeIdx = [log for log in rlog_list if log.which() == "roadEncodeIdx"]
roadEncodeIdx[0].roadEncodeIdx.to_dict()

{'frameId': 12002,
 'type': 'fullHEVC',
 'encodeId': 12000,
 'segmentNum': 10,
 'segmentId': 0,
 'segmentIdEncode': 0,
 'timestampSof': 1150939854090,
 'timestampEof': 1150954576278,
 'flags': 2147500040,
 'len': 104416}

In [85]:
# sentinel
sentinel = [log for log in rlog_list if log.which() == "sentinel"]
sentinel[0].sentinel.to_dict()

{'type': 'startOfSegment', 'signal': 0}

In [86]:
# temperatureSensor
temperatureSensor = [log for log in rlog_list if log.which() == "temperatureSensor"]
temperatureSensor[0].temperatureSensor.to_dict()

{'temperature': 55.94140625,
 'version': 1,
 'sensor': 0,
 'type': 13,
 'timestamp': 1151166302319,
 'source': 'lsm6ds3trc',
 'uncalibratedDEPRECATED': False}

In [87]:
# thumbnail
thumbnail = [log for log in rlog_list if log.which() == "thumbnail"]
thumbnail[0].thumbnail.to_dict()


{'frameId': 12003,
 'timestampEof': 1151004571538,
 'thumbnail': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00\x00\x01\x00\x01\x00\x00\xff\xdb\x00C\x00\x10\x0b\x0c\x0e\x0c\n\x10\x0e\r\x0e\x12\x11\x10\x13\x18(\x1a\x18\x16\x16\x181#%\x1d(:3=<9387@H\\N@DWE78PmQW_bghg>Mqypdx\\egc\xff\xdb\x00C\x01\x11\x12\x12\x18\x15\x18/\x1a\x1a/cB8Bcccccccccccccccccccccccccccccccccccccccccccccccccc\xff\xc0\x00\x11\x08\x01.\x01\xe2\x03\x01"\x00\x02\x11\x01\x03\x11\x01\xff\xc4\x00\x1f\x00\x00\x01\x05\x01\x01\x01\x01\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x01\x02\x03\x04\x05\x06\x07\x08\t\n\x0b\xff\xc4\x00\xb5\x10\x00\x02\x01\x03\x03\x02\x04\x03\x05\x05\x04\x04\x00\x00\x01}\x01\x02\x03\x00\x04\x11\x05\x12!1A\x06\x13Qa\x07"q\x142\x81\x91\xa1\x08#B\xb1\xc1\x15R\xd1\xf0$3br\x82\t\n\x16\x17\x18\x19\x1a%&\'()*456789:CDEFGHIJSTUVWXYZcdefghijstuvwxyz\x83\x84\x85\x86\x87\x88\x89\x8a\x92\x93\x94\x95\x96\x97\x98\x99\x9a\xa2\xa3\xa4\xa5\xa6\xa7\xa8\xa9\xaa\xb2\xb3\xb4\xb5\xb6\xb7\xb8\xb9\xba\xc2\xc3\xc4\xc5\xc6\xc7\x

In [88]:
# uiDebug
uiDebug = [log for log in rlog_list if log.which() == "uiDebug"]
uiDebug[0].uiDebug.to_dict()

{'drawTimeMillis': 3.6015100479125977}

In [89]:
# uiPlan
uiPlan = [log for log in rlog_list if log.which() == "uiPlan"]
uiPlan[0].uiPlan.to_dict()

{'position': {'x': [0.0,
   0.12735092639923096,
   0.5087607502937317,
   1.1427196264266968,
   2.0303544998168945,
   3.1643259525299072,
   4.560399055480957,
   6.218426704406738,
   8.124567031860352,
   10.297170639038086,
   12.755851745605469,
   15.522867202758789,
   18.610177993774414,
   22.0153865814209,
   25.743637084960938,
   29.868846893310547,
   34.37385940551758,
   39.22149658203125,
   44.47053909301758,
   50.19552230834961,
   56.35347366333008,
   62.94895935058594,
   70.0177001953125,
   77.56385040283203,
   85.69287109375,
   94.4241943359375,
   103.57501220703125,
   113.31536102294922,
   123.81005096435547,
   134.9630126953125,
   146.74896240234375,
   147.69091796875,
   147.69091796875],
  'y': [0.0,
   0.000155243236804381,
   0.0007949533173814416,
   0.002412038156762719,
   0.00580888194963336,
   0.01218397542834282,
   0.023183269426226616,
   0.04125384986400604,
   0.06854212284088135,
   0.10830315202474594,
   0.16530385613441467,
   0.2

In [90]:
# wideRoadCameraState
wideRoadCameraState = [log for log in rlog_list if log.which() == "wideRoadCameraState"]
wideRoadCameraState[0].wideRoadCameraState.to_dict()

{'frameId': 12003,
 'encodeId': 0,
 'timestampEof': 1151004688986,
 'frameLengthDEPRECATED': 0,
 'integLines': 158,
 'globalGainDEPRECATED': 0,
 'frameType': 'unknown',
 'timestampSof': 1150989924351,
 'lensPosDEPRECATED': 0,
 'lensSagDEPRECATED': 0.0,
 'lensErrDEPRECATED': 0.0,
 'lensTruePosDEPRECATED': 0.0,
 'gain': 7.320000171661377,
 'recoverStateDEPRECATED': 0,
 'highConversionGain': True,
 'measuredGreyFraction': 0.30078125,
 'targetGreyFraction': 0.3016214370727539,
 'processingTime': 0.010952135547995567,
 'frameIdSensor': 0,
 'sensor': 'ox03c10',
 'exposureValPercent': 0.5043274760246277,
 'requestId': 0}

In [91]:
# wideRoadEncodeIdx
wideRoadEncodeIdx = [log for log in rlog_list if log.which() == "wideRoadEncodeIdx"]
wideRoadEncodeIdx[0].wideRoadEncodeIdx.to_dict()

{'frameId': 12002,
 'type': 'fullHEVC',
 'encodeId': 12000,
 'segmentNum': 10,
 'segmentId': 0,
 'segmentIdEncode': 0,
 'timestampSof': 1150939905549,
 'timestampEof': 1150954717580,
 'flags': 2147500040,
 'len': 73270}

# NEW

In [80]:
# Huh, the rlog.json and qlog.json contains NaN values, but the loading doesn't crash because of it...
with open("rlog.json", "r") as f:
    rlog_json = json.load(f)
rlog_json

[{'initData': {'kernelArgs': ['rcupdate.rcu_expedited=1',
    'console=ttyMSM0,115200n8',
    'quiet',
    'loglevel=3',
    'earlycon=msm_geni_serial,0xA84000',
    'androidboot.hardware=qcom',
    'androidboot.console=ttyMSM0',
    'video=DSI-1:1080x2160@60e',
    'ehci-hcd.park=3',
    'lpm_levels.sleep_disabled=1',
    'service_locator.enable=1',
    'androidboot.selinux=permissive',
    'firmware_class.path=/lib/firmware/updates',
    'net.ifnames=0',
    'dyndbg=""',
    'root=/dev/sda6',
    'androidboot.bootdevice=1d84000.ufshc',
    'androidboot.serialno=9e856db5',
    'androidboot.baseband=sda',
    'msm_drm.dsi_display0=dsi_fhd_ea8074_1080_cmd_display:',
    'androidboot.slot_suffix=_a',
    'skip_initramfs',
    'rootwait',
    'ro',
    'init=/sbin/init'],
   'dongleId': '45ba82b7ecf23784',
   'deviceType': 'tizi',
   'version': '0.9.5-release',
   'dirty': False,
   'gitCommit': '0df64642759d61f59cc6f09b598ddadb7df96459',
   'gitBranch': 'release3',
   'passive': False,
 

# The difference between rlog and qlog

I am not entirely sure, but ChatGPT claims rlog is the Raw Logs, while the qlog is the quantized logs.
This means that qlog is a simplified version of the raw data. 

This is likely true as the original qlog file is much smaller than the rlog file. The json file for qlog is 20.8 MB while rlog.json is over 200 MB.